Before we get started, a couple of reminders to keep in mind when using iPython notebooks:

- Remember that you can see from the left side of a code cell when it was last run if there is a number within the brackets.
- When you start a new notebook session, make sure you run all of the cells up to the point where you last left off. Even if the output is still visible from when you ran the cells in your previous session, the kernel starts in a fresh state so you'll need to reload the data, etc. on a new session.
- The previous point is useful to keep in mind if your answers do not match what is expected in the lesson's quizzes. Try reloading the data and run all of the processing steps one by one in order to make sure that you are working with the same variables and data that are at each quiz stage.


## Load Data from CSVs

In [72]:
import unicodecsv

## Longer version of code (replaced with shorter, equivalent version below)

# enrollments = []
# f = open('enrollments.csv', 'rb')
# reader = unicodecsv.DictReader(f)
# for row in reader:
#     enrollments.append(row)
# f.close()

with open('enrollments.csv', 'rb') as f:
    reader = unicodecsv.DictReader(f)
    enrollments = list(reader)

In [73]:
#####################################
#                 1                 #
#####################################

## Read in the data from daily_engagement.csv and project_submissions.csv 
## and store the results in the below variables.
## Then look at the first row of each table.
import unicodecsv

with open('daily_engagement.csv', 'rb') as f:
    reader1 = unicodecsv.DictReader(f)
    daily_engagement = list(reader1)
print daily_engagement[0]
    
with open('project_submissions.csv', 'rb') as f:
    reader2 = unicodecsv.DictReader(f)
    project_submissions = list(reader2)
print project_submissions[0]

{u'lessons_completed': u'0.0', u'num_courses_visited': u'1.0', u'total_minutes_visited': u'11.6793745', u'projects_completed': u'0.0', u'acct': u'0', u'utc_date': u'2015-01-09'}
{u'lesson_key': u'3176718735', u'processing_state': u'EVALUATED', u'account_key': u'256', u'assigned_rating': u'UNGRADED', u'completion_date': u'2015-01-16', u'creation_date': u'2015-01-14'}


## Fixing Data Types

In [74]:
from datetime import datetime as dt

# Takes a date as a string, and returns a Python datetime object. 
# If there is no date given, returns None
def parse_date(date):
    if date == '':
        return None
    else:
        return dt.strptime(date, '%Y-%m-%d')
    
# Takes a string which is either an empty string or represents an integer,
# and returns an int or None.
def parse_maybe_int(i):
    if i == '':
        return None
    else:
        return int(i)

# Clean up the data types in the enrollments table
for enrollment in enrollments:
    enrollment['cancel_date'] = parse_date(enrollment['cancel_date'])
    enrollment['days_to_cancel'] = parse_maybe_int(enrollment['days_to_cancel'])
    enrollment['is_canceled'] = enrollment['is_canceled'] == 'True'
    enrollment['is_udacity'] = enrollment['is_udacity'] == 'True'
    enrollment['join_date'] = parse_date(enrollment['join_date'])
    
enrollments[0]

{u'account_key': u'448',
 u'cancel_date': datetime.datetime(2015, 1, 14, 0, 0),
 u'days_to_cancel': 65,
 u'is_canceled': True,
 u'is_udacity': True,
 u'join_date': datetime.datetime(2014, 11, 10, 0, 0),
 u'status': u'canceled'}

In [75]:
# Clean up the data types in the engagement table
for engagement_record in daily_engagement:
    engagement_record['lessons_completed'] = int(float(engagement_record['lessons_completed']))
    engagement_record['num_courses_visited'] = int(float(engagement_record['num_courses_visited']))
    engagement_record['projects_completed'] = int(float(engagement_record['projects_completed']))
    engagement_record['total_minutes_visited'] = float(engagement_record['total_minutes_visited'])
    engagement_record['utc_date'] = parse_date(engagement_record['utc_date'])
    
daily_engagement[0]

{u'acct': u'0',
 u'lessons_completed': 0,
 u'num_courses_visited': 1,
 u'projects_completed': 0,
 u'total_minutes_visited': 11.6793745,
 u'utc_date': datetime.datetime(2015, 1, 9, 0, 0)}

In [76]:
# Clean up the data types in the submissions table
for submission in project_submissions:
    submission['completion_date'] = parse_date(submission['completion_date'])
    submission['creation_date'] = parse_date(submission['creation_date'])

project_submissions[0]

{u'account_key': u'256',
 u'assigned_rating': u'UNGRADED',
 u'completion_date': datetime.datetime(2015, 1, 16, 0, 0),
 u'creation_date': datetime.datetime(2015, 1, 14, 0, 0),
 u'lesson_key': u'3176718735',
 u'processing_state': u'EVALUATED'}

Note when running the above cells that we are actively changing the contents of our data variables. If you try to run these cells multiple times in the same session, an error will occur.

## Investigating the Data

In [77]:
#####################################
#                 2                 #
#####################################

## Find the total number of rows and the number of unique students (account keys)
## in each table.
enrollment_num_rows = len(enrollments) 
list_of_unique_enrl_keys = []
for item in enrollments:
    if(int(item.get('account_key')) not in list_of_unique_enrl_keys):
        list_of_unique_enrl_keys.append(int(item.get('account_key')))
enrollment_num_unique_students = len(list_of_unique_enrl_keys)

engagement_num_rows = len(daily_engagement)
list_of_unique_eng_keys = []
for item in daily_engagement:
    if(int(item.get('acct')) not in list_of_unique_eng_keys):
        list_of_unique_eng_keys.append(int(item.get('acct')))
engagement_num_unique_students = len(list_of_unique_eng_keys)

submission_num_rows = len(project_submissions)             
list_of_unique_keys = []
for item in project_submissions:
    if(int(item.get('account_key')) not in list_of_unique_keys):
        list_of_unique_keys.append(int(item.get('account_key')))
submission_num_unique_students = len(list_of_unique_keys)

print enrollment_num_rows
print engagement_num_rows
print submission_num_rows

print enrollment_num_unique_students
print engagement_num_unique_students
print submission_num_unique_students


1640
136240
3642
1302
1237
743


## Problems in the Data

In [79]:
#####################################
#                 3                 #
#####################################

## Rename the "acct" column in the daily_engagement table to "account_key".
for item in daily_engagement:
    item['account_key'] = item.pop('acct')

0


## Missing Engagement Records

In [93]:
#####################################
#                 4                 #
#####################################

## Find any one student enrollments where the student is missing from the daily engagement table.
## Output that enrollment.
for item in daily_engagement:
    print "Account: " + str(item.get('account_key')) + "Lessons Finished: " + str(item.get('lessons_completed')) + "Minutes Spent: " + str(item.get('total_minutes_visited'))
    
# Some take-aways: 
# 1) Account=0 even though more than 1 lesson is finished. 
# 2) Account is always 0.
# 2) Some times time is spent even though the lesson is not finished.

Account: 0Lessons Finished: 0Minutes Spent: 11.6793745
Account: 0Lessons Finished: 0Minutes Spent: 37.2848873333
Account: 0Lessons Finished: 0Minutes Spent: 53.6337463333
Account: 0Lessons Finished: 0Minutes Spent: 33.4892696667
Account: 0Lessons Finished: 0Minutes Spent: 64.7796776667
Account: 0Lessons Finished: 1Minutes Spent: 151.617576833
Account: 0Lessons Finished: 0Minutes Spent: 142.395963833
Account: 0Lessons Finished: 0Minutes Spent: 0.0
Account: 0Lessons Finished: 0Minutes Spent: 9.8495625
Account: 0Lessons Finished: 0Minutes Spent: 38.330548
Account: 0Lessons Finished: 1Minutes Spent: 98.3275675
Account: 0Lessons Finished: 0Minutes Spent: 0.0
Account: 0Lessons Finished: 0Minutes Spent: 0.0
Account: 0Lessons Finished: 1Minutes Spent: 218.309690167
Account: 0Lessons Finished: 1Minutes Spent: 280.773319167
Account: 0Lessons Finished: 0Minutes Spent: 32.2760201667
Account: 0Lessons Finished: 0Minutes Spent: 65.467882
Account: 0Lessons Finished: 1Minutes Spent: 74.806089
Account:

Account: 3Lessons Finished: 0Minutes Spent: 0.0
Account: 3Lessons Finished: 0Minutes Spent: 0.0
Account: 3Lessons Finished: 0Minutes Spent: 0.0
Account: 3Lessons Finished: 0Minutes Spent: 0.0
Account: 3Lessons Finished: 0Minutes Spent: 0.0
Account: 3Lessons Finished: 0Minutes Spent: 0.0
Account: 3Lessons Finished: 0Minutes Spent: 0.0
Account: 3Lessons Finished: 0Minutes Spent: 0.0
Account: 3Lessons Finished: 0Minutes Spent: 0.0
Account: 3Lessons Finished: 0Minutes Spent: 0.0
Account: 3Lessons Finished: 0Minutes Spent: 0.0
Account: 3Lessons Finished: 0Minutes Spent: 0.0
Account: 4Lessons Finished: 0Minutes Spent: 0.0
Account: 4Lessons Finished: 0Minutes Spent: 0.0
Account: 4Lessons Finished: 0Minutes Spent: 0.0
Account: 4Lessons Finished: 0Minutes Spent: 33.3214046667
Account: 4Lessons Finished: 0Minutes Spent: 0.0
Account: 4Lessons Finished: 0Minutes Spent: 0.0
Account: 4Lessons Finished: 0Minutes Spent: 0.0
Account: 4Lessons Finished: 0Minutes Spent: 0.0
Account: 4Lessons Finished: 0M

Account: 13Lessons Finished: 0Minutes Spent: 0.0
Account: 13Lessons Finished: 0Minutes Spent: 0.0
Account: 14Lessons Finished: 0Minutes Spent: 0.0
Account: 14Lessons Finished: 0Minutes Spent: 0.0
Account: 14Lessons Finished: 0Minutes Spent: 65.6221875
Account: 14Lessons Finished: 0Minutes Spent: 0.0
Account: 14Lessons Finished: 0Minutes Spent: 0.0
Account: 14Lessons Finished: 0Minutes Spent: 0.0
Account: 14Lessons Finished: 0Minutes Spent: 0.0
Account: 14Lessons Finished: 1Minutes Spent: 60.7803568333
Account: 14Lessons Finished: 0Minutes Spent: 0.0
Account: 14Lessons Finished: 0Minutes Spent: 0.0
Account: 14Lessons Finished: 0Minutes Spent: 3.17969466667
Account: 14Lessons Finished: 0Minutes Spent: 0.0
Account: 14Lessons Finished: 0Minutes Spent: 0.0
Account: 14Lessons Finished: 0Minutes Spent: 0.0
Account: 14Lessons Finished: 0Minutes Spent: 0.0
Account: 14Lessons Finished: 0Minutes Spent: 0.0
Account: 14Lessons Finished: 0Minutes Spent: 0.0
Account: 14Lessons Finished: 0Minutes Spen

Account: 25Lessons Finished: 0Minutes Spent: 0.0
Account: 25Lessons Finished: 0Minutes Spent: 0.0
Account: 25Lessons Finished: 0Minutes Spent: 0.0
Account: 25Lessons Finished: 0Minutes Spent: 0.0
Account: 25Lessons Finished: 0Minutes Spent: 0.0
Account: 25Lessons Finished: 0Minutes Spent: 0.0
Account: 25Lessons Finished: 0Minutes Spent: 0.0
Account: 25Lessons Finished: 0Minutes Spent: 0.0
Account: 25Lessons Finished: 0Minutes Spent: 0.0
Account: 25Lessons Finished: 0Minutes Spent: 0.0
Account: 26Lessons Finished: 1Minutes Spent: 106.192694
Account: 26Lessons Finished: 0Minutes Spent: 0.0
Account: 26Lessons Finished: 0Minutes Spent: 96.8780855
Account: 26Lessons Finished: 0Minutes Spent: 0.0
Account: 26Lessons Finished: 0Minutes Spent: 0.0
Account: 26Lessons Finished: 0Minutes Spent: 0.0
Account: 26Lessons Finished: 1Minutes Spent: 227.730896333
Account: 26Lessons Finished: 0Minutes Spent: 0.0
Account: 26Lessons Finished: 0Minutes Spent: 0.0
Account: 26Lessons Finished: 0Minutes Spent: 

Account: 33Lessons Finished: 0Minutes Spent: 0.0
Account: 33Lessons Finished: 0Minutes Spent: 0.0
Account: 33Lessons Finished: 0Minutes Spent: 0.0
Account: 33Lessons Finished: 0Minutes Spent: 15.3809586667
Account: 33Lessons Finished: 0Minutes Spent: 84.864424
Account: 33Lessons Finished: 0Minutes Spent: 0.0
Account: 33Lessons Finished: 0Minutes Spent: 23.7553198333
Account: 33Lessons Finished: 0Minutes Spent: 0.0
Account: 33Lessons Finished: 0Minutes Spent: 54.8155053333
Account: 33Lessons Finished: 0Minutes Spent: 4.83215633333
Account: 33Lessons Finished: 0Minutes Spent: 0.0
Account: 33Lessons Finished: 0Minutes Spent: 0.0
Account: 33Lessons Finished: 0Minutes Spent: 0.0
Account: 33Lessons Finished: 0Minutes Spent: 50.1783948333
Account: 33Lessons Finished: 0Minutes Spent: 16.1298018333
Account: 33Lessons Finished: 0Minutes Spent: 26.7887498333
Account: 33Lessons Finished: 0Minutes Spent: 0.0
Account: 33Lessons Finished: 0Minutes Spent: 0.0
Account: 33Lessons Finished: 1Minutes Spen

...

Account: 1115Lessons Finished: 0Minutes Spent: 0.0
Account: 1115Lessons Finished: 0Minutes Spent: 0.0
Account: 1115Lessons Finished: 0Minutes Spent: 0.0
Account: 1115Lessons Finished: 0Minutes Spent: 0.0
Account: 1115Lessons Finished: 0Minutes Spent: 0.0
Account: 1115Lessons Finished: 0Minutes Spent: 0.0
Account: 1115Lessons Finished: 0Minutes Spent: 0.0
Account: 1115Lessons Finished: 0Minutes Spent: 0.0
Account: 1115Lessons Finished: 0Minutes Spent: 0.0
Account: 1115Lessons Finished: 0Minutes Spent: 0.0
Account: 1115Lessons Finished: 0Minutes Spent: 0.0
Account: 1115Lessons Finished: 0Minutes Spent: 0.0
Account: 1115Lessons Finished: 0Minutes Spent: 0.0
Account: 1115Lessons Finished: 0Minutes Spent: 0.0
Account: 1115Lessons Finished: 0Minutes Spent: 0.0
Account: 1115Lessons Finished: 0Minutes Spent: 0.0
Account: 1116Lessons Finished: 0Minutes Spent: 34.7048365
Account: 1116Lessons Finished: 0Minutes Spent: 4.62923983333
Account: 1117Lessons Finished: 0Minutes Spent: 0.0
Account: 1117L

Account: 1151Lessons Finished: 0Minutes Spent: 0.0
Account: 1151Lessons Finished: 0Minutes Spent: 0.0
Account: 1151Lessons Finished: 0Minutes Spent: 0.0
Account: 1151Lessons Finished: 0Minutes Spent: 0.0
Account: 1151Lessons Finished: 0Minutes Spent: 0.0
Account: 1151Lessons Finished: 0Minutes Spent: 0.0
Account: 1151Lessons Finished: 0Minutes Spent: 0.0
Account: 1151Lessons Finished: 0Minutes Spent: 0.0
Account: 1151Lessons Finished: 0Minutes Spent: 0.0
Account: 1151Lessons Finished: 0Minutes Spent: 0.0
Account: 1151Lessons Finished: 0Minutes Spent: 0.0
Account: 1151Lessons Finished: 0Minutes Spent: 0.0
Account: 1151Lessons Finished: 0Minutes Spent: 0.0
Account: 1151Lessons Finished: 0Minutes Spent: 0.0
Account: 1151Lessons Finished: 0Minutes Spent: 0.0
Account: 1151Lessons Finished: 0Minutes Spent: 0.0
Account: 1151Lessons Finished: 0Minutes Spent: 0.0
Account: 1151Lessons Finished: 0Minutes Spent: 0.0
Account: 1151Lessons Finished: 0Minutes Spent: 0.0
Account: 1151Lessons Finished: 

Account: 1189Lessons Finished: 0Minutes Spent: 0.0
Account: 1189Lessons Finished: 0Minutes Spent: 0.0
Account: 1189Lessons Finished: 0Minutes Spent: 0.0
Account: 1189Lessons Finished: 0Minutes Spent: 0.0
Account: 1189Lessons Finished: 0Minutes Spent: 0.0
Account: 1189Lessons Finished: 0Minutes Spent: 0.0
Account: 1189Lessons Finished: 0Minutes Spent: 0.0
Account: 1189Lessons Finished: 0Minutes Spent: 0.0
Account: 1189Lessons Finished: 0Minutes Spent: 0.0
Account: 1189Lessons Finished: 0Minutes Spent: 0.0
Account: 1189Lessons Finished: 0Minutes Spent: 0.0
Account: 1189Lessons Finished: 0Minutes Spent: 0.0
Account: 1192Lessons Finished: 0Minutes Spent: 0.0
Account: 1192Lessons Finished: 0Minutes Spent: 0.0
Account: 1192Lessons Finished: 0Minutes Spent: 0.0
Account: 1192Lessons Finished: 0Minutes Spent: 0.0
Account: 1192Lessons Finished: 0Minutes Spent: 0.0
Account: 1193Lessons Finished: 0Minutes Spent: 2.5272585
Account: 1193Lessons Finished: 0Minutes Spent: 3.254841
Account: 1193Lessons

Account: 1243Lessons Finished: 0Minutes Spent: 0.0
Account: 1243Lessons Finished: 0Minutes Spent: 0.0
Account: 1243Lessons Finished: 0Minutes Spent: 0.0
Account: 1243Lessons Finished: 0Minutes Spent: 0.0
Account: 1243Lessons Finished: 0Minutes Spent: 0.0
Account: 1244Lessons Finished: 0Minutes Spent: 0.0
Account: 1244Lessons Finished: 0Minutes Spent: 0.0
Account: 1244Lessons Finished: 0Minutes Spent: 0.0
Account: 1244Lessons Finished: 0Minutes Spent: 0.0
Account: 1244Lessons Finished: 0Minutes Spent: 0.0
Account: 1244Lessons Finished: 0Minutes Spent: 0.0
Account: 1244Lessons Finished: 0Minutes Spent: 0.0
Account: 1244Lessons Finished: 0Minutes Spent: 0.0
Account: 1244Lessons Finished: 0Minutes Spent: 0.0
Account: 1244Lessons Finished: 0Minutes Spent: 0.0
Account: 1244Lessons Finished: 0Minutes Spent: 0.0
Account: 1244Lessons Finished: 0Minutes Spent: 0.0
Account: 1244Lessons Finished: 0Minutes Spent: 0.0
Account: 1244Lessons Finished: 0Minutes Spent: 0.0
Account: 1244Lessons Finished: 

Account: 1267Lessons Finished: 0Minutes Spent: 0.0
Account: 1267Lessons Finished: 0Minutes Spent: 0.0
Account: 1267Lessons Finished: 0Minutes Spent: 0.0
Account: 1267Lessons Finished: 0Minutes Spent: 0.0
Account: 1267Lessons Finished: 0Minutes Spent: 0.0
Account: 1267Lessons Finished: 0Minutes Spent: 0.0
Account: 1267Lessons Finished: 0Minutes Spent: 0.0
Account: 1267Lessons Finished: 0Minutes Spent: 0.0
Account: 1267Lessons Finished: 0Minutes Spent: 0.0
Account: 1267Lessons Finished: 0Minutes Spent: 0.0
Account: 1267Lessons Finished: 0Minutes Spent: 0.0
Account: 1267Lessons Finished: 0Minutes Spent: 0.0
Account: 1267Lessons Finished: 0Minutes Spent: 0.0
Account: 1267Lessons Finished: 0Minutes Spent: 0.0
Account: 1267Lessons Finished: 0Minutes Spent: 0.0
Account: 1267Lessons Finished: 0Minutes Spent: 0.0
Account: 1267Lessons Finished: 0Minutes Spent: 0.0
Account: 1267Lessons Finished: 0Minutes Spent: 0.0
Account: 1267Lessons Finished: 0Minutes Spent: 0.0
Account: 1267Lessons Finished: 

## Checking for More Problem Records

In [ ]:
#####################################
#                 5                 #
#####################################

## Find the number of surprising data points (enrollments missing from
## the engagement table) that remain, if any.

## Tracking Down the Remaining Problems

In [ ]:
# Create a set of the account keys for all Udacity test accounts
udacity_test_accounts = set()
for enrollment in enrollments:
    if enrollment['is_udacity']:
        udacity_test_accounts.add(enrollment['account_key'])
len(udacity_test_accounts)

In [ ]:
# Given some data with an account_key field, removes any records corresponding to Udacity test accounts
def remove_udacity_accounts(data):
    non_udacity_data = []
    for data_point in data:
        if data_point['account_key'] not in udacity_test_accounts:
            non_udacity_data.append(data_point)
    return non_udacity_data

In [ ]:
# Remove Udacity test accounts from all three tables
non_udacity_enrollments = remove_udacity_accounts(enrollments)
non_udacity_engagement = remove_udacity_accounts(daily_engagement)
non_udacity_submissions = remove_udacity_accounts(project_submissions)

print len(non_udacity_enrollments)
print len(non_udacity_engagement)
print len(non_udacity_submissions)

## Refining the Question

In [ ]:
#####################################
#                 6                 #
#####################################

## Create a dictionary named paid_students containing all students who either
## haven't canceled yet or who remained enrolled for more than 7 days. The keys
## should be account keys, and the values should be the date the student enrolled.

paid_students =

## Getting Data from First Week

In [ ]:
# Takes a student's join date and the date of a specific engagement record,
# and returns True if that engagement record happened within one week
# of the student joining.
def within_one_week(join_date, engagement_date):
    time_delta = engagement_date - join_date
    return time_delta.days < 7

In [ ]:
#####################################
#                 7                 #
#####################################

## Create a list of rows from the engagement table including only rows where
## the student is one of the paid students you just found, and the date is within
## one week of the student's join date.

paid_engagement_in_first_week = 

## Exploring Student Engagement

In [ ]:
from collections import defaultdict

# Create a dictionary of engagement grouped by student.
# The keys are account keys, and the values are lists of engagement records.
engagement_by_account = defaultdict(list)
for engagement_record in paid_engagement_in_first_week:
    account_key = engagement_record['account_key']
    engagement_by_account[account_key].append(engagement_record)

In [ ]:
# Create a dictionary with the total minutes each student spent in the classroom during the first week.
# The keys are account keys, and the values are numbers (total minutes)
total_minutes_by_account = {}
for account_key, engagement_for_student in engagement_by_account.items():
    total_minutes = 0
    for engagement_record in engagement_for_student:
        total_minutes += engagement_record['total_minutes_visited']
    total_minutes_by_account[account_key] = total_minutes

In [ ]:
import numpy as np

# Summarize the data about minutes spent in the classroom
total_minutes = total_minutes_by_account.values()
print 'Mean:', np.mean(total_minutes)
print 'Standard deviation:', np.std(total_minutes)
print 'Minimum:', np.min(total_minutes)
print 'Maximum:', np.max(total_minutes)

## Debugging Data Analysis Code

In [ ]:
#####################################
#                 8                 #
#####################################

## Go through a similar process as before to see if there is a problem.
## Locate at least one surprising piece of data, output it, and take a look at it.

## Lessons Completed in First Week

In [ ]:
#####################################
#                 9                 #
#####################################

## Adapt the code above to find the mean, standard deviation, minimum, and maximum for
## the number of lessons completed by each student during the first week. Try creating
## one or more functions to re-use the code above.

## Number of Visits in First Week

In [ ]:
######################################
#                 10                 #
######################################

## Find the mean, standard deviation, minimum, and maximum for the number of
## days each student visits the classroom during the first week.

## Splitting out Passing Students

In [ ]:
######################################
#                 11                 #
######################################

## Create two lists of engagement data for paid students in the first week.
## The first list should contain data for students who eventually pass the
## subway project, and the second list should contain data for students
## who do not.

subway_project_lesson_keys = ['746169184', '3176718735']

passing_engagement =
non_passing_engagement =

## Comparing the Two Student Groups

In [ ]:
######################################
#                 12                 #
######################################

## Compute some metrics you're interested in and see how they differ for
## students who pass the subway project vs. students who don't. A good
## starting point would be the metrics we looked at earlier (minutes spent
## in the classroom, lessons completed, and days visited).

## Making Histograms

In [ ]:
######################################
#                 13                 #
######################################

## Make histograms of the three metrics we looked at earlier for both
## students who passed the subway project and students who didn't. You
## might also want to make histograms of any other metrics you examined.

## Improving Plots and Sharing Findings

In [ ]:
######################################
#                 14                 #
######################################

## Make a more polished version of at least one of your visualizations
## from earlier. Try importing the seaborn library to make the visualization
## look better, adding axis labels and a title, and changing one or more
## arguments to the hist() function.